# Trips - processing
Broad to-do:
- ~~consolidate csv to one trip per row~~ done in tsrtc8
- drop trips with blank or odd timings
- generate gtfs calendar.txt, trips.txt and stop_times.txt

In [1]:
import pandas as pd
from collections import OrderedDict
import numpy as np
import openpyxl
import os.path
from ast import literal_eval # for parsing list stored as string back into list
from save2Excel import save2Excel

/mnt/7ACA0CC0CA0C7B21/temp/py36/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


In [2]:
# loading the tripwise-gouped raw file
df = pd.read_csv('grouped-tripwise-raw.csv', dtype=str, index_col='sr').fillna('')
# typecasting all columns as text, so that concat etc operations are simpler to do further along.
print(df.shape)
df.columns

(35657, 29)


Index(['TRIP_ID', 'DEPOT_CODE', 'SERVICE_ID', 'SERVICE_NO', 'SERVICE_TYPE',
       'DAY_NIGHT_OUT', 'SCHEDULE_DAYS', 'ROUTE_ID', 'ROUTE_NUMBER',
       'TRIP_NUM', 'TRIP_TYPE', 'STAGE_ID', 'CURRENT_STAGE_NAME', 'num_stops',
       'STAGE_TYPE', 'DISTANCE', 'TIME_DISTANCE', 'FROM_TIME', 'first_time',
       'TO_TIME', 'BREAK_TIME', 'OPERATIONAL_DAYS', 'OD_MON', 'OD_TUE',
       'OD_WED', 'OD_THU', 'OD_FRI', 'OD_SAT', 'OD_SUN'],
      dtype='object')

In [3]:
'#'*100

'####################################################################################################'

## intervention from tsrtc7 file for dropping trips with missing or odd timings

In [4]:
# parse FROM_TIME string column to make it back to the list format it originally was.
# from https://stackoverflow.com/a/17796482/4355695
print( 'FROM_TIME before:',type(df.FROM_TIME.iloc[0]))
df['FROM_TIME'] = df.FROM_TIME.apply(lambda x: literal_eval(x))
print( 'FROM_TIME after:',type(df.FROM_TIME.iloc[0]))
print( df.FROM_TIME.iloc[0] )

FROM_TIME before: <class 'str'>
FROM_TIME after: <class 'list'>
['20:35', '20:39', '20:43', '20:48', '20:52', '20:57', '21:01', '21:06', '21:10', '21:15']


## check for blank timings

In [5]:
def checkBlankTimes(row):
    arr = row['FROM_TIME']
    if not isinstance(arr,list):
        print('\nTrip %s: FROM_TIME is not a list:'%row.TRIP_ID, arr)
    
    if ('' in arr) or (' ' in arr):
        print('#'*100,'\nTrip %s, route %s: FROM_TIME has one or more blanks:\n'%(row.TRIP_ID,row.ROUTE_NUMBER), arr)
        # print('Full row:',row)
        # print(row.TO_TIME, row.first_time)
        if row.TO_TIME != '':
            print('But TO_TIME is NOT blank:',row.TO_TIME)
            # nyet, not happening with this data.
        
    elif row.TO_TIME == '':
        print('Trip %s, route %s: no blanks in FROM_TIME, but TO_TIME is blank.'%(row.TRIP_ID,row.ROUTE_NUMBER))
        # not happening in this data.
    
    return None

# so, come to think of it, row.TO_TIME == '' is our condition for rows with blank timings.

In [6]:
a = df.apply(lambda row: checkBlankTimes(row), axis=1)

#################################################################################################### 
Trip 82427, route 94U: FROM_TIME has one or more blanks:
 ['', '', '', '', '', '']
#################################################################################################### 
Trip 96745, route 567: FROM_TIME has one or more blanks:
 ['', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '']
#################################################################################################### 
Trip 96746, route 567: FROM_TIME has one or more blanks:
 ['', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '']
#################################################################################################### 
Trip 96747, route 567: FROM_TIME has one or more blanks:
 ['', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', 

#### > blank timings analysis:
- 5 trips total have banks in them. 
- And they're ALL blanks, not mixed. 
- Good, this is not as bad as I'd anticipated.
- There's one trip from route 94U, and 4 trips from route 567.
- What to do about them? Well, without any timings data these guys are ghosts in the shell.

### > decision about trips with blank timings : DROP them.

`df.TO_TIME == ''` is our condition for finding all with blank timings.


In [7]:
df[df.TO_TIME == ''].index

Int64Index([26747, 35218, 35219, 35220, 35221], dtype='int64', name='sr')

In [8]:
df2 = df.drop( df[df.TO_TIME == ''].index )
# have to pass indexes to df.drop , can't use just query. but, can use query to get the indexes to drop yo!
# df2

In [9]:
print(df.shape,df2.shape)

(35657, 29) (35652, 29)


### > removed trips with blanks in timings

In [10]:
df2.columns

Index(['TRIP_ID', 'DEPOT_CODE', 'SERVICE_ID', 'SERVICE_NO', 'SERVICE_TYPE',
       'DAY_NIGHT_OUT', 'SCHEDULE_DAYS', 'ROUTE_ID', 'ROUTE_NUMBER',
       'TRIP_NUM', 'TRIP_TYPE', 'STAGE_ID', 'CURRENT_STAGE_NAME', 'num_stops',
       'STAGE_TYPE', 'DISTANCE', 'TIME_DISTANCE', 'FROM_TIME', 'first_time',
       'TO_TIME', 'BREAK_TIME', 'OPERATIONAL_DAYS', 'OD_MON', 'OD_TUE',
       'OD_WED', 'OD_THU', 'OD_FRI', 'OD_SAT', 'OD_SUN'],
      dtype='object')

## trips where length is only 2

In [11]:
# there are no trips where length is only 1
df2[df2.num_stops.astype(int) < 2].shape

(0, 29)

In [12]:
df2[df2.num_stops.astype(int) < 3].ROUTE_NUMBER.unique()

array(['MGBS-TIRUPATI', '1Z', '45F', '9F', 'B.PALLY-ATNR', '1B', '3H/N',
       '190R', '113YK', '45RF', '6G', 'VJA', '158F/VSN', '10AS', '10F',
       'KP', '19S/F', '19K/A', '158YF'], dtype=object)

In [13]:
df2[ (df2.num_stops.astype(int) < 3)].FROM_TIME

sr
219      [16:00, 02:35]
647      [06:50, 07:10]
649      [07:10, 07:40]
650      [07:45, 08:45]
652      [08:50, 09:50]
655      [10:05, 11:15]
657      [11:20, 12:30]
660      [12:35, 13:10]
662      [13:10, 13:45]
736      [06:20, 06:35]
737      [06:40, 07:10]
738      [07:15, 08:15]
739      [08:20, 09:20]
740      [09:35, 10:45]
741      [10:50, 12:00]
742      [12:05, 12:40]
743      [12:40, 13:15]
744      [13:20, 13:55]
782      [13:15, 13:50]
783      [13:50, 14:25]
794      [13:05, 13:40]
795      [13:40, 14:15]
872      [13:25, 14:00]
873      [14:00, 14:35]
874      [12:25, 13:00]
875      [13:00, 13:35]
876      [12:55, 13:30]
877      [12:15, 12:50]
878      [12:50, 13:25]
879      [13:30, 14:05]
              ...      
22349    [07:30, 08:20]
22350    [15:15, 16:05]
22351    [05:20, 05:40]
22352    [05:40, 06:30]
22353    [06:35, 07:25]
22355    [07:30, 08:20]
22356    [08:25, 09:15]
22357    [09:30, 10:40]
22358    [10:45, 11:55]
22360    [11:55, 12:10]
22365    [13:

### > there are 793 trips with length of 2 stops.
What to do about them:  
Let's let them be, and if the second timing drops, then assume it's rolling over to next day.

In [14]:
'#'*100

'####################################################################################################'

## Finding and Handling trips with odd timings
- see https://stackoverflow.com/a/3755251/4355695 for ascending / descending check.
- it may be better to simply covert ALL the timings into integers and run a check on them.
- for trips crossing over midnight: have to detect it, and add 24 hrs from that point onwards.
- Reversal doubt: there might be a case where it's the original trip sequence that's been given wrong, and the reversed timings might be flagging that rather than the timings being wrong.
- And then there's really odd stuff out there.
- So, better to flag, store and drop out the trips with odd timings.

In [15]:
def time2number(t, rollover=0):
    if not isinstance(t,str):
        print('Hey! this time value',t,'is not a string!')
        return 0
    if len(t) != 5:
        print('Hey! this time value',t,'isn\'t formatted properly!')
        return 0
    anotherday = 0 if (rollover==0) else (60*24)
    return int(t[:2])*60 + int(t[3:]) + anotherday

In [16]:
def makeNumberTimings(arr):
    if not isinstance(arr,list):
        print('Hey! this is not a list!',arr)
        return arr
    
    nextDayThreshold = -12*60 # keeping a 12-hr threshold
    rollover = 0
    timenumCollect = []
    for n in range(len(arr)):
        
        if n > 0 and rollover==0 : # this will only happen once
            timediff = time2number(arr[n]) - timenumCollect[-1]
            if timediff <= nextDayThreshold: #super-negative!
                rollover = 1
        timenumCollect.append( time2number( arr[n],rollover ) )
    
    return timenumCollect

In [17]:
df2['FROM_TIME_num'] = df2.FROM_TIME.apply(makeNumberTimings)
df2['FROM_TIME_num']

sr
0        [1235, 1239, 1243, 1248, 1252, 1257, 1261, 126...
1                                [454, 454, 454, 469, 469]
2                                [469, 469, 469, 559, 559]
3                                [589, 589, 679, 679, 679]
4                                [709, 709, 709, 799, 799]
5                                [829, 829, 919, 919, 919]
6                              [949, 949, 949, 1039, 1039]
7                           [1069, 1069, 1159, 1159, 1159]
8                           [1159, 1159, 1174, 1174, 1174]
9                                [467, 467, 467, 482, 482]
10                               [482, 482, 482, 572, 572]
11                               [602, 602, 692, 692, 692]
12                               [722, 722, 722, 812, 812]
13                               [842, 842, 932, 932, 932]
14                             [962, 962, 962, 1052, 1052]
15                          [1082, 1082, 1172, 1172, 1172]
16                          [1172, 1172, 1187, 1187, 

#### > Observation: after dropping blanks, conversion of timings to numbers happened smoothly, all time values were properly formatted like 'hh:mm'.

In [18]:
'#'*100

'####################################################################################################'

### oh, one more thing : have to reflect the rollover back to the timings column
.. actually lets create a new column to store the midnight-adjusted values

In [19]:
def number2time(n):
    mm = n % 60
    hh = n // 60
    # padding zeros in case single digit or zero. from https://stackoverflow.com/a/339013/4355695
    return '%02d:%02d'%(hh,mm) 

def number2timeList(arr):
    return [number2time(x) for x in arr]

In [20]:
df2['FROM_TIME_NEW'] = df2.FROM_TIME_num.apply(number2timeList)

In [21]:
df2['FROM_TIME_NEW'].sample(10)

sr
27024                  [13:50, 13:54, 13:58, 14:07, 14:15]
34293    [18:35, 18:40, 18:46, 18:52, 18:58, 19:04, 19:...
23851    [12:36, 12:37, 12:41, 12:44, 12:46, 12:52, 12:...
800      [17:25, 17:31, 17:38, 17:45, 17:51, 17:58, 18:...
7213     [17:13, 17:17, 17:22, 17:27, 17:32, 17:37, 17:...
10244    [16:10, 16:10, 16:10, 16:10, 16:10, 16:10, 16:...
21632    [08:00, 08:00, 08:02, 08:05, 08:08, 08:10, 08:...
18740    [09:16, 09:20, 09:24, 09:29, 09:33, 09:37, 09:...
19671    [07:40, 07:43, 07:46, 07:49, 07:52, 07:55, 07:...
8818     [20:30, 20:35, 20:35, 20:38, 21:26, 21:26, 21:...
Name: FROM_TIME_NEW, dtype: object

In [22]:
'#'*100

'####################################################################################################'

## show cases where the rollover has happened:
greater than 23:59, >> 1439 mins

In [23]:
df2['crossMidnight'] = df2.FROM_TIME_num.apply(lambda arr: True if max(arr) > 1439 else False)

In [24]:
df2[ df2['crossMidnight'] == True].shape

(29, 32)

In [25]:
# seriously? only 29?? all that trouble for...
df2[ df2['crossMidnight']][['ROUTE_NUMBER','TRIP_ID','FROM_TIME','FROM_TIME_NEW']]

ROUTE_NUMBER TRIP_ID  \
sr                              
219     MGBS-TIRUPATI  115356   
428        PALAMANERU  118101   
446        PALAMANERU  118172   
486               NDL  118268   
1199     B.PALLY-ATNR  136221   
8539       VIJAYAWADA   53730   
8544           ONGOLE   53735   
8547           ONGOLE   53740   
8552       MARKAPURAM   53745   
9502       VIJAYAWADA   55869   
9856    MGBS-TIRUPATI   56630   
14633             VJA   64509   
14667             VJA   64548   
15206             242   65162   
15876              9F   65955   
17021     PULIVENDULA   67425   
17063     ECIL-GUNTUR   67496   
17069     ECIL-GUNTUR   67502   
17318              B1   67806   
17375              B1   67898   
17400              B1   67923   
17447              B1   68011   
17482              B1   68071   
25451        MYP-WGLL   80395   
25665         MYP-GDK   80743   
25725        MYP-KRMR   80882   
27525         MYP-VJA   83492   
32492  NIZAMABAD-ARSP   90286   
32679        WARANGAL   90503   

                                               FROM_TIME  \
sr                                                         
219                                       [16:00, 02:35]   
428    [22:45, 09:44, 02:25, 02:25, 02:25, 02:25, 02:25]   
446    [23:00, 23:00, 23:00, 23:00, 23:00, 15:48, 03:00]   
486    [23:50, 23:50, 23:50, 23:50, 23:50, 23:50, 23:...   
1199                                      [19:35, 03:15]   
8539                               [22:15, 21:50, 03:35]   
8544                               [20:00, 03:13, 02:55]   
8547                               [21:00, 20:41, 03:40]   
8552                               [21:00, 03:41, 03:20]   
9502                               [22:15, 21:50, 03:35]   
9856                                      [20:20, 07:00]   
14633                                     [22:15, 00:10]   
14667                                     [23:15, 01:10]   
15206                [22:50, 21:13, 20:24, 06:42, 00:15]   
15876                                     [23:45, 00:00]   
17021                [21:45, 21:15, 20:55, 19:41, 01:45]   
17063         [23:00, 05:44, 05:14, 05:07, 04:37, 04:30]   
17069         [22:45, 05:29, 04:59, 04:52, 04:22, 04:15]   
17318  [23:45, 05:39, 02:49, 00:00, 00:00, 00:00, 00:00]   
17375  [23:00, 05:40, 02:57, 00:15, 00:15, 00:15, 00:15]   
17400  [22:45, 05:25, 02:42, 00:00, 00:00, 00:00, 00:00]   
17447  [23:00, 05:40, 02:57, 00:15, 00:15, 00:15, 00:15]   
17482  [23:00, 23:00, 23:00, 23:00, 20:17, 17:35, 00:15]   
25451  [23:00, 17:31, 16:18, 15:05, 01:42, 01:28, 01:...   
25665         [23:35, 23:25, 23:16, 23:06, 03:30, 03:30]   
25725         [23:40, 23:40, 01:41, 01:26, 01:10, 00:55]   
27525                              [22:00, 02:18, 02:15]   
32492         [22:55, 20:50, 19:37, 03:44, 00:08, 00:05]   
32679         [23:15, 22:02, 21:06, 03:21, 00:29, 00:25]   

                                           FROM_TIME_NEW  
sr                                                        
219                                       [16:00, 26:35]  
428    [22:45, 33:44, 26:25, 26:25, 26:25, 26:25, 26:25]  
446    [23:00, 23:00, 23:00, 23:00, 23:00, 15:48, 27:00]  
486    [23:50, 23:50, 23:50, 23:50, 23:50, 23:50, 23:...  
1199                                      [19:35, 27:15]  
8539                               [22:15, 21:50, 27:35]  
8544                               [20:00, 27:13, 26:55]  
8547                               [21:00, 20:41, 27:40]  
8552                               [21:00, 27:41, 27:20]  
9502                               [22:15, 21:50, 27:35]  
9856                                      [20:20, 31:00]  
14633                                     [22:15, 24:10]  
14667                                     [23:15, 25:10]  
15206                [22:50, 21:13, 20:24, 30:42, 24:15]  
15876                                     [23:45, 24:00]  
17021                [21:45, 21:15, 20:55, 19:41, 25:45]  
17063         [23:00, 29:44, 29:14, 29:07, 28:37, 28:30]  
170

#### > still got to filter out odd timings. lets flag these crossMidnight trips in the analysis part.

In [26]:
'#'*100

'####################################################################################################'

### after converting to numeric, now checking for ascending timings

In [27]:
def checkAscending(l):
    return all(l[i] <= l[i+1] for i in range(len(l)-1))
    # from https://stackoverflow.com/a/3755251/4355695

In [28]:
df2['timingsOK'] = df2.FROM_TIME_num.apply(checkAscending)

In [29]:
df2[df2.timingsOK != True].shape

(102, 33)

In [30]:
df2[df2.timingsOK != True][['TRIP_ID','ROUTE_NUMBER','FROM_TIME','FROM_TIME_num','timingsOK']]

TRIP_ID    ROUTE_NUMBER  \
sr                              
428    118101      PALAMANERU   
446    118172      PALAMANERU   
486    118268             NDL   
550    119144            9Y/F   
1060   123280              M1   
1499    15164              8A   
2145    18636            DVRM   
2147    18638            DVRM   
2149    18668          KADAPA   
2152    18671          KADAPA   
2439    19609              5K   
3018    21750              A1   
3041    21788              A1   
3058    21817              A2   
3072    21833              A2   
3101    21862              A2   
4219    24849          KADAPA   
4330    25508          KADAPA   
4526    33849              A1   
4862    37508           107JD   
5121    37973          16A-XC   
6313    48869              A1   
8539    53730      VIJAYAWADA   
8544    53735          ONGOLE   
8547    53740          ONGOLE   
8552    53745      MARKAPURAM   
8914    54418             83J   
9502    55869      VIJAYAWADA   
9670    56173     THADIPATHRI   
9673    56176     THADIPATHRI   
...       ...             ...   
22879   76175             488   
23670   77273            251P   
24725   79203             219   
25214   80022         MYP-NZB   
25234   80048        VJA-ATNR   
25242   80063        VJA-ATNR   
25272   80103            201K   
25280   80122        VJA-ATNR   
25303   80151        VJA-ATNR   
25310   80159        VJA-ATNR   
25451   80395        MYP-WGLL   
25490   80458        VJA-ATNR   
25611   80632        VJA-ATNR   
25626   80647        VJA-ATNR   
25665   80743         MYP-GDK   
25725   80882        MYP-KRMR   
27311   83207             290   
27525   83492         MYP-VJA   
27792   83847             208   
27962   84048            226L   
28166   84339             VJA   
32284   90053             10H   
32330   90107             10H   
32492   90286  NIZAMABAD-ARSP   
32679   90503        WARANGAL   
33352   91529         212/702   
33954   92339              9M   
34952   96048            118D   
35044   96192            288D   
35292   96941             90L   

                                               FROM_TIME  \
sr                                                         
428    [22:45, 09:44, 02:25, 02:25, 02:25, 02:25, 02:25]   
446    [23:00, 23:00, 23:00, 23:00, 23:00, 15:48, 03:00]   
486    [23:50, 23:50, 23:50, 23:50, 23:50, 23:50, 23:...   
550    [13:55, 13:53, 13:52, 13:51, 13:50, 13:49, 13:...   
1060   [23:05, 17:52, 13:11, 09:32, 07:27, 04:20, 03:...   
1499   [17:35, 17:34, 17:32, 17:32, 17:32, 17:32, 17:...   
2145   [16:30, 16:30, 16:14, 13:09, 08:30, 06:26, 04:...   
2147   [17:30, 17:30, 17:14, 14:07, 09:24, 07:19, 05:...   
2149   [17:20, 17:20, 17:06, 14:29, 12:39, 11:57, 10:...   
2152   [21:00, 19:50, 16:10, 14:51, 12:15, 10:50, 10:...   
2439   [23:00, 20:42, 18:24, 16:06, 13:48, 11:30, 09:...   
3018   [23:00, 21:53, 19:40, 17:28, 13:36, 08:37, 06:...   
3041   [23:00, 16:57, 14:46, 09:49, 05:59, 03:47, 01:...   
3058   [22:30, 21:24, 17:33, 15:54, 15:21, 09:19, 04:...   
3072   [23:30, 22:24, 18:33, 16:54, 16:21, 10:19, 05:...   
3101   [22:30, 17:33, 13:10, 07:08, 06:35, 04:56, 01:...   
4219   [20:15, 20:15, 20:01, 17:27, 15:40, 14:59, 13:...   
4330   [23:00, 23:00, 22:46, 20:08, 18:18, 17:35, 16:...   
4526   [22:50, 21:44, 19:32, 17:20, 13:30, 08:33, 06:...   
4862   [13:55, 13:53, 13:51, 13:50, 13:48, 13:46, 13:...   
5121   [23:25, 22:37, 19:26, 16:15, 13:04, 09:53, 06:...   
6313   [23:30, 17:25, 15:12, 10:13, 06:21, 04:09, 01:...   
8539                               [22:15, 21:50, 03:35]   
8544                               [20:00, 03:13, 02:55]   
8547                               [21:00, 20:41, 03:40]   
8552                               [21:00, 03:41, 03:20]   
8914          [10:05, 10:04, 10:04, 10:04, 10:04, 10:04]   
9502                               [22:15, 21:50, 03:35]   
9670                 [23:50, 18:20, 15:27, 09:08, 03:55]   
9673                 [20:45, 15:31, 09:12, 06:19, 00:50]   
...   

In [31]:
# example:
print(df2.iloc[486].FROM_TIME)
print(df2.iloc[486].FROM_TIME_NEW)

['23:50', '23:50', '23:50', '23:50', '23:50', '23:50', '23:50', '23:50', '23:50', '23:41', '03:50']
['23:50', '23:50', '23:50', '23:50', '23:50', '23:50', '23:50', '23:50', '23:50', '23:41', '27:50']


In [32]:
# Routes under which these odd trips are there
a = df2[df2.timingsOK != True].ROUTE_NUMBER.unique()
print('Route numbers having trips with odd timings:',len(a))
print(a)

Route numbers having trips with odd timings: 58
['PALAMANERU' 'NDL' '9Y/F' 'M1' '8A' 'DVRM' 'KADAPA' '5K' 'A1' 'A2'
 '107JD' '16A-XC' 'VIJAYAWADA' 'ONGOLE' 'MARKAPURAM' '83J' 'THADIPATHRI'
 '115' '16A' '502' 'BGLR' '242' '201 G/I' '242RG' '113K/L' 'VJA' 'GUNTUR'
 'PULIVENDULA' 'ECIL-TPT' 'ECIL-GUNTUR' 'ECIL-AMALAPURAM' 'ECIL-RAZOLE'
 'B1' 'P1' '219' '29B/272I' '218C' '288D' '253M' '488' '251P' 'MYP-NZB'
 'VJA-ATNR' '201K' 'MYP-WGLL' 'MYP-GDK' 'MYP-KRMR' '290' 'MYP-VJA' '208'
 '226L' '10H' 'NIZAMABAD-ARSP' 'WARANGAL' '212/702' '9M' '118D' '90L']


In [33]:
# grouping by routes, sorting by count
df2[df2.timingsOK != True].groupby('ROUTE_NUMBER').TRIP_ID.count().sort_values(ascending=False)

ROUTE_NUMBER
VJA-ATNR           8
218C               6
B1                 5
VJA                4
A1                 4
KADAPA             4
29B/272I           3
A2                 3
288D               2
5K                 2
BGLR               2
DVRM               2
ECIL-AMALAPURAM    2
ECIL-GUNTUR        2
ECIL-RAZOLE        2
ECIL-TPT           2
219                2
113K/L             2
PALAMANERU         2
VIJAYAWADA         2
THADIPATHRI        2
ONGOLE             2
10H                2
253M               1
251P               1
242RG              1
242                1
226L               1
212/702            1
208                1
115                1
118D               1
16A                1
16A-XC             1
201 G/I            1
201K               1
290                1
WARANGAL           1
9Y/F               1
488                1
MYP-KRMR           1
PULIVENDULA        1
P1                 1
NIZAMABAD-ARSP     1
NDL                1
MYP-WGLL           1
MYP-VJA            1


these oddballs will be better off analysed manually rather than trying to rectify programmatically right now.
### > 102 trips in 58 routes found with odd timings

### let's save out the odd-timings trips and drop them from the main df for further steps

In [34]:
dfOddTimings = df2[df2.timingsOK != True].copy()

In [35]:
# dfOddTimings.head()

In [36]:
dfOddTimings.to_csv('trips-with-OddTimings.csv')
# also, remember to add this to excel at the end

In [37]:
save2Excel(dfOddTimings,'Trips_OddTimings')

Existing sheets in TSRTC-analysis.xlsx : ['Stops_Repeating', 'Stops_Grouping', 'ServiceType_Stops', 'Route_id_depot_listing', 'Routes_repeating', 'Routes_sameDepot']
Sheet Trips_OddTimings added to TSRTC-analysis.xlsx


In [38]:
# make new df with odd timings omitted
df3 = df2[df2.timingsOK == True].copy()
# using .copy() because further down, when creating new cols etc it was giving warnings 
# as this was still a slice of the original df2. now with .copy() it's a whole new dataframe.

In [39]:
'#'*100

'####################################################################################################'

## calendar

In [40]:
df3[['OD_MON', 'OD_TUE', 'OD_WED', 'OD_THU', 'OD_FRI', 'OD_SAT', 'OD_SUN']].drop_duplicates()

OD_MON OD_TUE OD_WED OD_THU OD_FRI OD_SAT OD_SUN
sr                                                    
0          Y      Y      Y      Y      Y      Y      Y
50         N      N      N      N      N      N      Y
150        N      N      N      N      N      N      N
198        N      N      N      N      N      Y      Y
213        Y      Y      Y      Y      Y      Y      N
381        Y      N      N      Y      Y      Y      Y
1241       Y      Y      Y      Y      Y      N      N
2565       N      N      N      Y      Y      Y      Y
3416       Y      Y      Y      Y      Y      N      Y
6197       Y      Y      Y      N      Y      Y      Y
8077       Y      Y      N      Y      Y      Y      Y
8546       N      N      N      Y      N      N      N
10112      N      N      N      Y      N      N      Y
10432      Y      N      N      N      N      N      N
10966      Y      N      N      N      N      N      Y
15128      N      Y      Y      Y      Y      Y      Y
15744      N      N      N      N      Y      N      Y
16513      N      N      N      N      Y      Y      Y
16544      Y      Y      N      Y      Y      Y      N
16654      Y      N      Y      Y      Y      Y      N
17018      Y      N      N      Y      Y      Y      N
18439      Y      N      Y      Y      Y      Y      Y
20405      Y      N      N      N      Y      Y      Y
22351      N      N      N      N      Y      N      N
22366      N      N      N      N      N      Y      N
23176      N      N      N      N      Y      Y      N
27737      Y      Y      Y      N      Y      N      N
28956      Y      Y      Y      Y      N      Y      Y
30585      Y      N      N      N      N      Y      Y

### oh crap they're all over the place. let's programmatically make the calendar id's..

In [41]:
def calendar_service_naming(x):
    '''
    to do: zap the day's letter if it's not on that day.
    '''
    cal_service_id = '@MoTuWeThFrSaSu'
    if x['OD_MON'] == 'N': cal_service_id = cal_service_id.replace('Mo','')
    if x['OD_TUE'] == 'N': cal_service_id = cal_service_id.replace('Tu','')
    if x['OD_WED'] == 'N': cal_service_id = cal_service_id.replace('We','')
    if x['OD_THU'] == 'N': cal_service_id = cal_service_id.replace('Th','')
    if x['OD_FRI'] == 'N': cal_service_id = cal_service_id.replace('Fr','')
    if x['OD_SAT'] == 'N': cal_service_id = cal_service_id.replace('Sa','')
    if x['OD_SUN'] == 'N': cal_service_id = cal_service_id.replace('Su','')
    return cal_service_id

In [42]:
df3['gtfs_calendar_id'] = df3.apply( calendar_service_naming, axis=1)

In [43]:
df3.columns

Index(['TRIP_ID', 'DEPOT_CODE', 'SERVICE_ID', 'SERVICE_NO', 'SERVICE_TYPE',
       'DAY_NIGHT_OUT', 'SCHEDULE_DAYS', 'ROUTE_ID', 'ROUTE_NUMBER',
       'TRIP_NUM', 'TRIP_TYPE', 'STAGE_ID', 'CURRENT_STAGE_NAME', 'num_stops',
       'STAGE_TYPE', 'DISTANCE', 'TIME_DISTANCE', 'FROM_TIME', 'first_time',
       'TO_TIME', 'BREAK_TIME', 'OPERATIONAL_DAYS', 'OD_MON', 'OD_TUE',
       'OD_WED', 'OD_THU', 'OD_FRI', 'OD_SAT', 'OD_SUN', 'FROM_TIME_num',
       'FROM_TIME_NEW', 'crossMidnight', 'timingsOK', 'gtfs_calendar_id'],
      dtype='object')

In [44]:
# check it out!
df3[[ 'OD_MON', 'OD_TUE', 'OD_WED', 'OD_THU', 'OD_FRI',
       'OD_SAT', 'OD_SUN', 'gtfs_calendar_id' ]].drop_duplicates('gtfs_calendar_id')

OD_MON OD_TUE OD_WED OD_THU OD_FRI OD_SAT OD_SUN gtfs_calendar_id
sr                                                                     
0          Y      Y      Y      Y      Y      Y      Y  @MoTuWeThFrSaSu
50         N      N      N      N      N      N      Y              @Su
150        N      N      N      N      N      N      N                @
198        N      N      N      N      N      Y      Y            @SaSu
213        Y      Y      Y      Y      Y      Y      N    @MoTuWeThFrSa
381        Y      N      N      Y      Y      Y      Y      @MoThFrSaSu
1241       Y      Y      Y      Y      Y      N      N      @MoTuWeThFr
2565       N      N      N      Y      Y      Y      Y        @ThFrSaSu
3416       Y      Y      Y      Y      Y      N      Y    @MoTuWeThFrSu
6197       Y      Y      Y      N      Y      Y      Y    @MoTuWeFrSaSu
8077       Y      Y      N      Y      Y      Y      Y    @MoTuThFrSaSu
8546       N      N      N      Y      N      N      N              @Th
10112      N      N      N      Y      N      N      Y            @ThSu
10432      Y      N      N      N      N      N      N              @Mo
10966      Y      N      N      N      N      N      Y            @MoSu
15128      N      Y      Y      Y      Y      Y      Y    @TuWeThFrSaSu
15744      N      N      N      N      Y      N      Y            @FrSu
16513      N      N      N      N      Y      Y      Y          @FrSaSu
16544      Y      Y      N      Y      Y      Y      N      @MoTuThFrSa
16654      Y      N      Y      Y      Y      Y      N      @MoWeThFrSa
17018      Y      N      N      Y      Y      Y      N        @MoThFrSa
18439      Y      N      Y      Y      Y      Y      Y    @MoWeThFrSaSu
20405      Y      N      N      N      Y      Y      Y        @MoFrSaSu
22351      N      N      N      N      Y      N      N              @Fr
22366      N      N      N      N      N      Y      N              @Sa
23176      N      N      N      N      Y      Y      N            @FrSa
27737      Y      Y      Y      N      Y      N      N        @MoTuWeFr
28956      Y      Y      Y      Y      N      Y      Y    @MoTuWeThSaSu
30585      Y      N      N      N      N      Y      Y          @MoSaSu

### now, like the tail wagging the dog, let's generate the calendar.txt from the id's generated

In [45]:
gtfs_calendar_ids_list = df3.gtfs_calendar_id.unique().tolist()

In [46]:
calendar_collector = []
for oneID in gtfs_calendar_ids_list:
    oneRow = OrderedDict()
    oneRow['service_id'] = oneID
    oneRow['monday'] = 1 if 'Mo' in oneID else 0
    oneRow['tuesday'] = 1 if 'Tu' in oneID else 0
    oneRow['wednesday'] = 1 if 'We' in oneID else 0
    oneRow['thursday'] = 1 if 'Th' in oneID else 0
    oneRow['friday'] = 1 if 'Fr' in oneID else 0
    oneRow['saturday'] = 1 if 'Sa' in oneID else 0
    oneRow['sunday'] = 1 if 'Su' in oneID else 0
    calendar_collector.append(oneRow.copy())
calendarDF = pd.DataFrame(calendar_collector)
calendarDF['start_date'] = '20180730'
calendarDF['end_date'] = '20990101'

In [47]:
calendarDF

service_id  monday  tuesday  wednesday  thursday  friday  saturday  \
0   @MoTuWeThFrSaSu       1        1          1         1       1         1   
1               @Su       0        0          0         0       0         0   
2                 @       0        0          0         0       0         0   
3             @SaSu       0        0          0         0       0         1   
4     @MoTuWeThFrSa       1        1          1         1       1         1   
5       @MoThFrSaSu       1        0          0         1       1         1   
6       @MoTuWeThFr       1        1          1         1       1         0   
7         @ThFrSaSu       0        0          0         1       1         1   
8     @MoTuWeThFrSu       1        1          1         1       1         0   
9     @MoTuWeFrSaSu       1        1          1         0       1         1   
10    @MoTuThFrSaSu       1        1          0         1       1         1   
11              @Th       0        0          0         1       0         0   
12            @ThSu       0        0          0         1       0         0   
13              @Mo       1        0          0         0       0         0   
14            @MoSu       1        0          0         0       0         0   
15    @TuWeThFrSaSu       0        1          1         1       1         1   
16            @FrSu       0        0          0         0       1         0   
17          @FrSaSu       0        0          0         0       1         1   
18      @MoTuThFrSa       1        1          0         1       1         1   
19      @MoWeThFrSa       1        0          1         1       1         1   
20        @MoThFrSa       1        0          0         1       1         1   
21    @MoWeThFrSaSu       1        0          1         1       1         1   
22        @MoFrSaSu       1        0          0         0       1         1   
23              @Fr       0        0          0         0       1         0   
24              @Sa       0        0          0         0       0         1   
25            @FrSa       0        0          0         0       1         1   
26        @MoTuWeFr       1        1          1         0       1         0   
27    @MoTuWeThSaSu       1        1          1         1       0         1   
28          @MoSaSu       1        0          0         0       0         1   

    sunday start_date  end_date  
0        1   20180730  20990101  
1        1   20180730  20990101  
2        0   20180730  20990101  
3        1   20180730  20990101  
4        0   20180730  20990101  
5        1   20180730  20990101  
6        0   20180730  20990101  
7        1   20180730  20990101  
8        1   20180730  20990101  
9        1   20180730  20990101  
10       1   20180730  20990101  
11       0   20180730  20990101  
12       1   20180730  20990101  
13       0   20180730  20990101  
14       1   20180730  20990101  
15       1   20180730  20990101  
16       1   20180730  20990101  
17       1   20180730  20990101  
18       0   20180730  20990101  
19       0   20180730  20990101  
20       0   20180730  20990101  
21       1   20180730  20990101  
22       1   20180730  20990101  
23       0   20180730  20990101  
24       0   20180730  20990101  
25       0   20180730  20990101  
26       0   20180730  20990101  
27       1   20180730  20990101  
28       1   20180730  20990101

In [48]:
calendarDF.to_csv('calendar.txt', index=False)

### > created gtfs calendar.txt

In [49]:
'#'*100

'####################################################################################################'

## creating gtfs trips.txt

In [50]:
df3['gtfs_direction_id'] = df3.TRIP_TYPE.apply( lambda x: '0' if x=='U' else '1')
df3[['gtfs_direction_id','TRIP_TYPE']].head()

gtfs_direction_id TRIP_TYPE
sr                            
0                  1         D
1                  0         U
2                  0         U
3                  1         D
4                  0         U

In [51]:
df3['trip_short_name'] = df3.apply( lambda row: \
    row['ROUTE_NUMBER'] + ': ' + row['FROM_TIME_NEW'][0] + ' ' + row['TRIP_TYPE'], axis=1 )
df3[[ 'trip_short_name','ROUTE_NUMBER','FROM_TIME_NEW' ]].head()

trip_short_name ROUTE_NUMBER  \
sr                                
0      2J: 20:35 D           2J   
1    222L: 07:34 U         222L   
2    222L: 07:49 U         222L   
3    222L: 09:49 D         222L   
4    222L: 11:49 U         222L   

                                        FROM_TIME_NEW  
sr                                                     
0   [20:35, 20:39, 20:43, 20:48, 20:52, 20:57, 21:...  
1                 [07:34, 07:34, 07:34, 07:49, 07:49]  
2                 [07:49, 07:49, 07:49, 09:19, 09:19]  
3                 [09:49, 09:49, 11:19, 11:19, 11:19]  
4                 [11:49, 11:49, 11:49, 13:19, 13:19]

In [52]:
# ok we have what we need to generate trips.txt
# TSRTC's SERVICE_ID is taken as gtfs block_id
tripsDF = df3[['ROUTE_ID','gtfs_calendar_id','TRIP_ID','trip_short_name','gtfs_direction_id','SERVICE_NO']]\
    .rename(columns={ 'ROUTE_ID':'route_id', 'gtfs_calendar_id':'service_id', 'TRIP_ID':'trip_id', 'gtfs_direction_id':'direction_id','SERVICE_NO':'block_id' })

tripsDF = tripsDF.sort_values(['route_id','service_id','trip_id'])
tripsDF

route_id       service_id trip_id   trip_short_name direction_id  \
sr                                                                       
16179    10007  @MoTuWeThFrSaSu   66311    19K/A: 12:15 U            0   
16180    10007  @MoTuWeThFrSaSu   66312    19K/A: 12:30 U            0   
16183    10007  @MoTuWeThFrSaSu   66315    19K/A: 13:35 D            1   
16186    10007  @MoTuWeThFrSaSu   66318    19K/A: 14:40 U            0   
16188    10007  @MoTuWeThFrSaSu   66320    19K/A: 15:45 D            1   
16191    10007  @MoTuWeThFrSaSu   66323    19K/A: 16:50 U            0   
16217    10007  @MoTuWeThFrSaSu   66351    19K/A: 18:05 D            1   
16218    10007  @MoTuWeThFrSaSu   66352    19K/A: 19:10 U            0   
16219    10007  @MoTuWeThFrSaSu   66353    19K/A: 20:15 D            1   
16220    10007  @MoTuWeThFrSaSu   66354    19K/A: 05:25 U            0   
16225    10007  @MoTuWeThFrSaSu   66362    19K/A: 06:40 D            1   
16226    10007  @MoTuWeThFrSaSu   66365    19K/A: 07:55 U            0   
16227    10007  @MoTuWeThFrSaSu   66367    19K/A: 09:20 D            1   
16228    10007  @MoTuWeThFrSaSu   66369    19K/A: 10:20 D            1   
17343    10021    @MoTuWeThFrSa   67847  156/118: 15:00 U            0   
17347    10021    @MoTuWeThFrSa   67856  156/118: 07:00 U            0   
17348    10021    @MoTuWeThFrSa   67858  156/118: 09:05 D            1   
17349    10021    @MoTuWeThFrSa   67859  156/118: 10:20 U            0   
17350    10021    @MoTuWeThFrSa   67862  156/118: 11:40 D            1   
17366    10021    @MoTuWeThFrSa   67888  156/118: 16:50 D            1   
17367    10021    @MoTuWeThFrSa   67889  156/118: 18:20 U            0   
17368    10021    @MoTuWeThFrSa   67890  156/118: 19:40 D            1   
25218    10022      @MoThFrSaSu   80028  MYP-NZB: 08:25 U            0   
25220    10022      @MoThFrSaSu   80031  MYP-NZB: 08:45 U            0   
25221    10022      @MoThFrSaSu   80032  MYP-NZB: 09:45 U            0   
25222    10022      @MoThFrSaSu   80033  MYP-NZB: 12:15 U            0   
25225    10022      @MoThFrSaSu   80037  MYP-NZB: 13:25 D            1   
25226    10022      @MoThFrSaSu   80038  MYP-NZB: 13:45 D            1   
25227    10022      @MoThFrSaSu   80039  MYP-NZB: 16:15 D            1   
25228    10022      @MoThFrSaSu   80040  MYP-NZB: 17:15 D            1   
...        ...              ...     ...               ...          ...   
25081     9990  @MoTuWeThFrSaSu   79774    30KPK: 10:00 U            0   
25082     9990  @MoTuWeThFrSaSu   79775    30KPK: 12:40 D            1   
25083     9990  @MoTuWeThFrSaSu   79776    30KPK: 15:25 U            0   
25084     9990  @MoTuWeThFrSaSu   79777    30KPK: 18:25 D            1   
25092     9990            @SaSu   79786    30KPK: 07:15 U            0   
25098     9990            @SaSu   79812    30KPK: 07:30 D            1   
25100     9990            @SaSu   79817    30KPK: 10:45 U            0   
25101     9990            @SaSu   79819    30KPK: 13:25 D            1   
25109     9990            @SaSu   79828    30KPK: 16:10 U            0   
25110     9990            @SaSu   79830    30KPK: 19:10 D            1   
14612     9997            @SaSu   64476      VJA: 09:30 U            0   
14613     9997            @SaSu   64478      VJA: 09:40 U            0   
14616     9997            @SaSu   64483      VJA: 10:50 U            0   
14617     9997            @SaSu   64485      VJA: 13:20 U            0   
14618     9997            @SaSu   64486      VJA: 14:10 U            0   
14633     9997            @SaSu   64509      VJA: 22:15 D            1   
14636     9997            @SaSu   64514      VJA: 00:20 D            1   
14639     9997            @SaSu   64518      VJA: 01:10 D            1   
14644     9997            @SaSu   64525      VJA: 03:40 D            1   
14646     9997            @SaSu   64527      VJA: 04:15 D            1   
14652     9997            @SaSu   64533      VJA: 12:00 U            0   
14655     

In [53]:
tripsDF.to_csv('trips.txt',index=False)

### > gtfs trips.txt created

In [54]:
'#'*100

'####################################################################################################'

## stop_times

In [55]:
df3.columns

Index(['TRIP_ID', 'DEPOT_CODE', 'SERVICE_ID', 'SERVICE_NO', 'SERVICE_TYPE',
       'DAY_NIGHT_OUT', 'SCHEDULE_DAYS', 'ROUTE_ID', 'ROUTE_NUMBER',
       'TRIP_NUM', 'TRIP_TYPE', 'STAGE_ID', 'CURRENT_STAGE_NAME', 'num_stops',
       'STAGE_TYPE', 'DISTANCE', 'TIME_DISTANCE', 'FROM_TIME', 'first_time',
       'TO_TIME', 'BREAK_TIME', 'OPERATIONAL_DAYS', 'OD_MON', 'OD_TUE',
       'OD_WED', 'OD_THU', 'OD_FRI', 'OD_SAT', 'OD_SUN', 'FROM_TIME_num',
       'FROM_TIME_NEW', 'crossMidnight', 'timingsOK', 'gtfs_calendar_id',
       'gtfs_direction_id', 'trip_short_name'],
      dtype='object')

### before proceeding: certain columns supposed to be lists are still as strings.
eval them back into lists

In [56]:
if isinstance(df3.CURRENT_STAGE_NAME.iloc[0], str):
    print('Before:CURRENT_STAGE_NAME:',type(df3.CURRENT_STAGE_NAME.iloc[0]) )
    df3['CURRENT_STAGE_NAME'] = df3.CURRENT_STAGE_NAME.apply(lambda x: literal_eval(x))
    print('After:CURRENT_STAGE_NAME:',type(df3.CURRENT_STAGE_NAME.iloc[0]) )
else: print('CURRENT_STAGE_NAME: you\'re fine')

if isinstance(df3.STAGE_ID.iloc[0], str):
    print('Before:STAGE_ID:',type(df3.STAGE_ID.iloc[0]) )
    df3['STAGE_ID'] = df3.STAGE_ID.apply(lambda x: literal_eval(x))
    print('After:STAGE_ID:',type(df3.STAGE_ID.iloc[0]) )
else: print('STAGE_ID: you\'re fine')

Before:CURRENT_STAGE_NAME: <class 'str'>
After:CURRENT_STAGE_NAME: <class 'list'>
Before:STAGE_ID: <class 'str'>
After:STAGE_ID: <class 'list'>


In [57]:
collector = []
counter=0
for i,row in df3.iterrows():
    st = OrderedDict()
    st['trip_id'] = row['TRIP_ID']
    
    for n in range(len(row['CURRENT_STAGE_NAME'])):
        st['stop_sequence'] = (n+1)*10
        # why setting sequence as 10, 20 etc instead of 1,2 :
        # It's possible that there may be more stops between the "stages". We can leave gaps to fill later. 
        # GTFS doesn't mind the gaps in the stop_sequence, as long as they're all positive integers in ascending order.
        
        st['stop_id'] = row['STAGE_ID'][n]
        
        dep_array = row['FROM_TIME_NEW']
        
        timeStr = dep_array[n]+ ':00'
        hh = int(timeStr[:2])
        
        if n > 0:
            prev_hh = int( collector[-1]['arrival_time'][:2] )
            if hh < prev_hh:
                timeStr = str(hh+24) + timeStr[2:]
                
        st['arrival_time'] = st['departure_time'] = dep_array[n]+ ':00'
        collector.append(st.copy())

In [58]:
st

OrderedDict([('trip_id', '99'),
             ('stop_sequence', 100),
             ('stop_id', '14611'),
             ('arrival_time', '20:30:00'),
             ('departure_time', '20:30:00')])

In [59]:
stop_timesDF = pd.DataFrame(collector)
stop_timesDF['timepoint'] = '0'
stop_timesDF    

trip_id  stop_sequence stop_id arrival_time departure_time timepoint
0          100             10   14611     20:35:00       20:35:00         0
1          100             20   14610     20:39:00       20:39:00         0
2          100             30    8326     20:43:00       20:43:00         0
3          100             40   13260     20:48:00       20:48:00         0
4          100             50    8059     20:52:00       20:52:00         0
5          100             60    8345     20:57:00       20:57:00         0
6          100             70    6936     21:01:00       21:01:00         0
7          100             80    1997     21:06:00       21:06:00         0
8          100             90    1133     21:10:00       21:10:00         0
9          100            100     182     21:15:00       21:15:00         0
10      100059             10    6764     07:34:00       07:34:00         0
11      100059             20    8550     07:34:00       07:34:00         0
12      100059             30     688     07:34:00       07:34:00         0
13      100059             40    8501     07:49:00       07:49:00         0
14      100059             50    3484     07:49:00       07:49:00         0
15      100060             10    6764     07:49:00       07:49:00         0
16      100060             20     688     07:49:00       07:49:00         0
17      100060             30    8550     07:49:00       07:49:00         0
18      100060             40    3484     09:19:00       09:19:00         0
19      100060             50    8501     09:19:00       09:19:00         0
20      100081             10    3484     09:49:00       09:49:00         0
21      100081             20    8501     09:49:00       09:49:00         0
22      100081             30     688     11:19:00       11:19:00         0
23      100081             40    8550     11:19:00       11:19:00         0
24      100081             50    6764     11:19:00       11:19:00         0
25      100082             10    8550     11:49:00       11:49:00         0
26      100082             20     688     11:49:00       11:49:00         0
27      100082             30    6764     11:49:00       11:49:00         0
28      100082             40    8501     13:19:00       13:19:00         0
29      100082             50    3484     13:19:00       13:19:00         0
...        ...            ...     ...          ...            ...       ...
435829   98857             10    7636     09:45:00       09:45:00         0
435830   98857             20   14817     10:02:00       10:02:00         0
435831   98857             30    8073     10:47:00       10:47:00         0
435832   98857             40     142     11:45:00       11:45:00         0
435833   98858             10     142     11:50:00       11:50:00         0
435834   98858             20    8073     12:47:00       12:47:00         0
435835   98858             30   14817     13:32:00       13:32:00         0
435836   98858             40    7636     13:50:00       13:50:00         0
435837   98859             10    7636     14:05:00       14:05:00         0
435838   98859             20   14817     14:22:00       14:22:00         0
435839   98859             30    8073     15:07:00       15:07:00         0
435840   98859             40     142     16:05:00       16:05:00         0
435841   98860             10     142     16:10:00       16:10:00         0
435842   98860             20    8073     17:07:00       17:07:00         0
435843   98860             30   14817     17:52:00       17:52:00         0
435844   98860             40    7636     18:10:00       18:10:00         0
435845   98861             10    7636     18:15:00       18:15:00         0
435846   98861             20   14817     18:24:00       18:24:00         0
435847   98861             30    8073     18:48:00       18:48:00         0
435848   98861             40     142     19:20:00       19:20:00         0
435849      99             10     182     19:27:00     

In [60]:
stop_timesDF.to_csv('stop_times.txt', index=False)

### > gtfs stop_times.txt created

In [61]:
# saving the large tripwise table with its new columns added and odd-times trips dropped and all
df3.to_csv('grouped-tripwise.csv', index_label='sr')